# Sevilla + cloro

In [4]:
import folium
from folium import Choropleth, Circle, Marker, Icon, Map, TileLayer
from folium.plugins import HeatMap, MarkerCluster
import geopandas as gpd
import pandas as pd
import json
import ast

## cargamos el geojson:

In [118]:
geo_json = r"DATA/Barrios2.geojson"

with open (geo_json) as geo_file:
    sevi_barrios = json.load(geo_file)

## probamos a visualizarlo:

In [129]:
m = folium.Map(location=[37.39161,-5.97640], zoom_start=12, tiles='CartoDB positron')

folium.GeoJson(sevi_barrios).add_to(m)

m;

## buscamos la feature que nos interesa:

In [130]:
sevi_barrios["features"][25]["properties"]["Barrio"]

'EL PRADO-PARQUE MARIA LUISA'

In [142]:
sevi_barrios["features"][25]["properties"]["Superf_Ha"]

76.55981513

In [144]:
listajson=[(elem["properties"]["Barrio"],elem["properties"]["Superf_Ha"]) for elem in sevi_barrios["features"]]
listajson=sorted(listajson)
listajson

[('AEROPUERTO VIEJO', 514.61840326),
 ('ALFALFA', 33.49195361),
 ('AMATE', 25.44587449),
 ('ARBOL GORDO', 4.98475505501),
 ('ARENAL', 38.12146675),
 ('AVENIDA DE LA PAZ', 25.86449879),
 ('BAMI', 20.776162765),
 ('BARRIADA DE PINEDA', 112.48955582),
 ('BARRIADA PINO MONTANO', 149.600157945),
 ('BARRIO LEON', 15.11249215),
 ('BEGOÑA-SANTA CATALINA', 11.644592015),
 ('BELLAVISTA', 1165.63661556),
 ('CAMPOS DE SORIA', 11.460884115),
 ('CISNEO ALTO-SANTA MARIA DE GRACIA', 9.10836915499),
 ('CIUDAD JARDIN', 43.28696497),
 ('COLORES, ENTREPARQUES', 1331.23463722),
 ('CONSOLACION', 25.50425416),
 ('CRUZ ROJA-CAPUCHINOS', 25.51757732),
 ('DOCTOR BARRAQUER-GRUPO RENFE-POLICLINICO', 47.228001455),
 ('EL CARMEN', 4.37341718),
 ('EL CEREZO', 6.33501108999),
 ('EL CERRO', 65.058242645),
 ('EL FONTANAL-MARIA AUXILIADORA-CARRETERA DE CARMONA', 24.331558775),
 ('EL GORDILLO', 1179.35101736),
 ('EL JUNCAL-HISPALIS', 81.43862204),
 ('EL PLANTINAR', 24.234084635),
 ('EL PORVENIR', 33.63033973),
 ('EL PRAD

## cargamos el data:

In [170]:
df = pd.read_csv("DATA/sev_pobl.csv", index_col=0, encoding="latin-1")
df["HAB"]=df.HOMBRES+df.MUJERES
df.drop(columns=["SECCION"],inplace=True)
df.head()

BARRIO EDAD  HOMBRES  MUJERES  HAB
DISTRITO                                            
1         SANTA CATALINA   00        7        8   15
1         SANTA CATALINA   01        4        5    9
1         SANTA CATALINA   02        6        3    9
1         SANTA CATALINA   03        2        8   10
1         SANTA CATALINA   04        7       12   19

In [171]:
listadata=sorted(df.BARRIO.unique())

In [175]:
dicci={}                                   # tengo que hacerlo para seguir avanzando
for i in range(108):
    dicci[f"{listadata[i]}"]=f"{listajson[i]}"

In [176]:
df=df.replace(dicci)

In [177]:
df.head()

BARRIO EDAD  HOMBRES  MUJERES  HAB
DISTRITO                                                              
1         ('SANTA CATALINA', 21.771652825)   00        7        8   15
1         ('SANTA CATALINA', 21.771652825)   01        4        5    9
1         ('SANTA CATALINA', 21.771652825)   02        6        3    9
1         ('SANTA CATALINA', 21.771652825)   03        2        8   10
1         ('SANTA CATALINA', 21.771652825)   04        7       12   19

## agrupamos por barrio :

In [163]:
dfg = df.groupby(df.BARRIO, sort = False).sum()
dfg["Barrio"]=dfg.index
dfg["supfHas"]=dfg.index[1]
dfg["densi"]=dfg["Barrio"]/dfg["supfHas"]

dfg.head()

HOMBRES  MUJERES   HAB
BARRIO                                                  
('SANTA CATALINA', 21.771652825)     2103     2353  4456
('FERIA', 29.782087885)              3298     3367  6665
ENCARNACIÓN-REGINA                   1850     2427  4277
('SAN JULIAN', 25.822166925)         2891     3263  6154
('SAN VICENTE', 38.75566251)         2706     2986  5692

In [165]:
dfg.index

Index(['('SANTA CATALINA', 21.771652825)', '('FERIA', 29.782087885)',
       'ENCARNACIÓN-REGINA', '('SAN JULIAN', 25.822166925)',
       '('SAN VICENTE', 38.75566251)', '('SAN LORENZO', 36.276110685)',
       '('SAN GIL', 27.124654895)', '('MUSEO', 42.908769585)',
       '('ARENAL', 38.12146675)', '('SANTA CRUZ', 77.26065417)',
       ...
       '('PALACIO DE CONGRESOS, URBADIEZ, ENTREPUENTES', 315.23901043)',
       'PARQUE ALCOSA-JARDINES DEL EDÉN', '('BELLAVISTA', 1165.63661556)',
       '('SECTOR SUR-LA PALMERA-REINA MERCEDES', 151.498556685)',
       '('HELIOPOLIS', 34.84870621)',
       '('PEDRO SALVADOR-LAS PALMERITAS-GUADAIRA', 31.834423335)',
       '('BARRIADA DE PINEDA', 112.48955582)',
       '('ELCANO-BERMEJALES', 107.26685232)', '('TABLADA', 1332.01334969)',
       '('LOS REMEDIOS', 109.906628385)'],
      dtype='object', name='BARRIO', length=107)

## intentamos el coropl

In [198]:
sevilla_clo = folium.Map(location=[37.39161,-5.97640], zoom_start=12, tiles="cartodbpositron");

sevilla_clo.choropleth(
    geo_data = sevi_barrios,
    data = dfg, 
    columns = ["Barrio","HAB"],
    key_on = "feature.properties.Barrio", 
    fill_color = "YlGnBu",
    fill_opacity = 0.4,
    line_opacity = 1,
    legend_name = "Población total por barrios",
    smooth_factor = 1,
    highlight=True
    
)

sevilla_clo;

KeyError: "None of ['Barrio'] are in the columns"

# Vamos con las secciones:

In [178]:
geo_json = r"DATA/SeccCensales_2014_2015.geojson"

with open (geo_json) as geo_file:
    sev_secc = json.load(geo_file)

In [180]:
m = folium.Map(location=[37.39161,-5.97640], zoom_start=12, tiles='CartoDB positron')

folium.GeoJson(sev_secc).add_to(m)

m

## si exploramos el propio geojson...

In [181]:
sev_secc.keys()

dict_keys(['type', 'name', 'crs', 'features'])

In [182]:
len(sev_secc["features"])

606

In [184]:
sev_secc["features"][44]["properties"]

{'FID': 45,
 'Secc_6D': 64,
 'Secc_11D': 34,
 'SUP': 0.03975327715,
 'Perimetro': 1036.734008,
 'Distri_6D': 3,
 'Distri_11D': 8,
 'Barrio': 'SAN PABLO D Y E',
 'HabitTotal': 992,
 'FECHA': 0,
 'ACTUACION': ' ',
 'SECCION': '8-34',
 'OBSERVACIO': ' ',
 'ESTADO': 0,
 'HabitHombr': 469,
 'HabitMujer': 523,
 'USOS': ' ',
 'P_15_0_18': 173.0,
 'P_15_18_64': 628.0,
 'P_15_64': 204.0,
 'P_15_H': 464.0,
 'P_15_M': 541.0,
 'P_15_T': 1005.0,
 'CreationDate': '2015/12/01 13:16:02',
 'Creator': 'Ayto.Sevilla',
 'EditDate': '2015/12/01 13:16:02',
 'Editor': 'Ayto.Sevilla',
 'SHAPE_Length': 0.01053752176911604,
 'SHAPE_Area': 4.041759836990189e-06}

In [191]:
FIDs=[elem["properties"]["FID"] for elem in sev_secc["features"]]
Habitantes=[elem["properties"]["HabitTotal"] for elem in sev_secc["features"]]
Superficies=[elem["properties"]["SUP"] for elem in sev_secc["features"]]

In [194]:
df=pd.DataFrame(FIDs,columns=["FID"])
df["Habitantes"]=Habitantes
df["Superficie"]=Superficies
df["Densidad"]=df["Habitantes"]/df["Superficie"]

In [195]:
df

FID  Habitantes  Superficie      Densidad
0      1        1556    0.046335  33581.774618
1      2        1240    0.046264  26802.613847
2      3         687    0.046098  14902.948970
3      4        1397    0.045820  30488.972395
4      5        1767    0.045795  38585.242243
..   ...         ...         ...           ...
601  602        1632   10.627216    153.567969
602  603        1632   10.627216    153.567969
603  604        1632   10.627216    153.567969
604  605           0    0.251891      0.000000
605  606           0    2.178298      0.000000

[606 rows x 4 columns]

In [200]:
secc_cloro = folium.Map(location=[37.3882,-5.9699], zoom_start=13, tiles="cartodbpositron");

secc_cloro.choropleth(
    geo_data = sev_secc,
    data = df, 
    columns = ["FID", "Densidad"],
    key_on = "feature.properties.FID", 
    fill_color = "YlGnBu",
    fill_opacity = 0.4,
    line_opacity = 1,
    legend_name = "Valores de DENSIDAD",
    smooth_factor = 1,
    highlight=True
);

In [197]:
secc_cloro

# Vamos con las bicis:

In [201]:
geo_json2 = r"DATA/SEVICI.geojson"

with open (geo_json2) as geo_file:
    sev_SEVICI = json.load(geo_file)

In [204]:
folium.GeoJson(sev_SEVICI).add_to(secc_cloro);

In [205]:
secc_cloro

## probamos el heatmap:

In [207]:
mapa = folium.Map(location=[37.3882,-5.9699], zoom_start=13, tiles="cartodbpositron");

In [208]:
sev_SEVICI.keys()

dict_keys(['type', 'name', 'crs', 'features'])

In [209]:
bicis_gdf = gpd.read_file("DATA/SEVICI.geojson")

In [213]:
type(bicis_gdf)

geopandas.geodataframe.GeoDataFrame

In [211]:
bicis_gdf.sample()

FID  id_estacio                     Direccion              Aproximaci  \
193  194       109.0  Avenida San Francisco Javier  Calle Camilo José Cela   

         Lat_Y     Lon_X         CreationDate       Creator  \
193  37.379898 -5.974588  2014-10-04T21:21:32  Ayto.Sevilla   

                EditDate        Editor                   geometry  
193  2014-10-04T21:21:32  Ayto.Sevilla  POINT (-5.97459 37.37990)

In [225]:
bicis_gdf["x"]=bicis_gdf["geometry"].x
bicis_gdf["y"]=bicis_gdf["geometry"].y

In [226]:
bicis_gdf.sample()

FID  id_estacio          Direccion         Aproximaci      Lat_Y  \
84   85       173.0  Ronda Tamarguillo  Avenida de la Paz  37.370045   

       Lon_X         CreationDate       Creator             EditDate  \
84 -5.968101  2014-10-04T21:21:32  Ayto.Sevilla  2014-10-04T21:21:32   

          Editor                   geometry         x          y  
84  Ayto.Sevilla  POINT (-5.96810 37.37005) -5.968101  37.370045

In [228]:
locations = list(zip(bicis_gdf["y"], bicis_gdf["x"]))

In [229]:
HeatMap(locations).add_to(mapa)

In [230]:
mapa

In [ ]:
tarde[["lat", "lon"]]

In [224]:
biciFG = folium.FeatureGroup("Las Bicicletas")
HeatMap(data=bicis_gdf.geometry, radius=15).add_to(biciFG)
biciFG.add_to(mapa)

TypeError: 'Point' object is not subscriptable

In [ ]:
#rounding coordinates by chosen precision creates a grid
rounding_num=0.015 
df["lon_mod"]=np.round(df.longitude/rounding_num,0)*rounding_num

#adjusting for difference in actual distance between same numeric change in lat and lon to create a square grid
correction_coeff=0.5
df["lat_mod"]=np.round(df.latitude/(rounding_num*correction_coeff),0)*(rounding_num*correction_coeff)

df_map=df[["lat_mod","lon_mod","unit_price"]].groupby(["lat_mod","lon_mod"], as_index=False).mean()

df_map.head()